# Processing the data

In [0]:
import torch
import torchvision


In [13]:
print(torch.cuda.is_available())

True


In [0]:
import torch
import torch.nn as nn
from torch import optim
import torch.nn.functional as F
import csv
import random
import re
import os 
import unicodedata
import codecs
import itertools

In [0]:
CUDA = torch.cuda.is_available()
device = torch.device("cuda" if CUDA else 'cpu')

In [16]:
device

device(type='cuda')

In [0]:
lines_filepath = os.path.join('movie_lines.txt')
conv_filepath = os.path.join('movie_conversations.txt')

In [18]:
#Visualise some lines
with open(lines_filepath, 'rb') as file:
 lines = file.readlines()
for line in lines[:8]:
  print(line.strip())

b'L1045 +++$+++ u0 +++$+++ m0 +++$+++ BIANCA +++$+++ They do not!'
b'L1044 +++$+++ u2 +++$+++ m0 +++$+++ CAMERON +++$+++ They do to!'
b'L985 +++$+++ u0 +++$+++ m0 +++$+++ BIANCA +++$+++ I hope so.'
b'L984 +++$+++ u2 +++$+++ m0 +++$+++ CAMERON +++$+++ She okay?'
b"L925 +++$+++ u0 +++$+++ m0 +++$+++ BIANCA +++$+++ Let's go."
b'L924 +++$+++ u2 +++$+++ m0 +++$+++ CAMERON +++$+++ Wow'
b"L872 +++$+++ u0 +++$+++ m0 +++$+++ BIANCA +++$+++ Okay -- you're gonna need to learn how to lie."
b'L871 +++$+++ u2 +++$+++ m0 +++$+++ CAMERON +++$+++ No'


In [0]:
#splits each line of the file into a dictionary of fields (lineID, characterID, movieID, character, text)
line_fields = ['lineID', 'characterID', 'movieID', 'character', 'text']
lines = {}
with open(lines_filepath, 'r', encoding = 'iso-8859-1') as f:
  for line in f:
    values = line.split(' +++$+++ ')
    #Extract fields
    lineObj = {}
    for i, field in enumerate(line_fields):
      lineObj[field] = values[i]
    
    lines[lineObj['lineID']] = lineObj

In [20]:
len(lines.items())


304713

In [0]:
# Group fields of lines from "loadlines" into conversation based on "movie_conversation.txt"
conv_fields = ['character1ID', 'character2ID', 'movieID', 'utteranceIDs']
conversations = []
with open(conv_filepath, 'r', encoding = 'iso_8859-1') as f:
  for  line in f:
    values = line.split(' +++$+++ ')
    #Extract fields
    conv_obj = {}
    for i, field in enumerate(conv_fields):
      conv_obj[field] = values[i]
    #Convert string result from split to list, since conv_obj[utteranceIDs] == ['L1045', 'L2345',...]
    lineIds = eval(conv_obj['utteranceIDs'])
    
    #Reassemble lines 
    conv_obj['lines'] = []
    for lineId in lineIds:
      conv_obj['lines'].append(lines[lineId])
    conversations.append(conv_obj)


In [22]:
conversations[0]

{'character1ID': 'u0',
 'character2ID': 'u2',
 'lines': [{'character': 'BIANCA',
   'characterID': 'u0',
   'lineID': 'L194',
   'movieID': 'm0',
   'text': 'Can we make this quick?  Roxanne Korrine and Andrew Barrett are having an incredibly horrendous public break- up on the quad.  Again.\n'},
  {'character': 'CAMERON',
   'characterID': 'u2',
   'lineID': 'L195',
   'movieID': 'm0',
   'text': "Well, I thought we'd start with pronunciation, if that's okay with you.\n"},
  {'character': 'BIANCA',
   'characterID': 'u0',
   'lineID': 'L196',
   'movieID': 'm0',
   'text': 'Not the hacking and gagging and spitting part.  Please.\n'},
  {'character': 'CAMERON',
   'characterID': 'u2',
   'lineID': 'L197',
   'movieID': 'm0',
   'text': "Okay... then how 'bout we try out some French cuisine.  Saturday?  Night?\n"}],
 'movieID': 'm0',
 'utteranceIDs': "['L194', 'L195', 'L196', 'L197']\n"}

In [23]:
len(conversations)

83097

In [0]:
#Extract pairs of sentences from conversations 
qa_pairs = []
for conversation in conversations:
  #iterate over all the sentences 
  for i in range(len(conversation['lines']) - 1):
    input_text = conversation['lines'][i]['text'].strip()
    output_text = conversation['lines'][i + 1]['text'].strip()
    #filter wrong samples (if one of the lists is empty)
    if input_text and output_text:
      qa_pairs.append([input_text, output_text])


In [25]:
qa_pairs[1]

["Well, I thought we'd start with pronunciation, if that's okay with you.",
 'Not the hacking and gagging and spitting part.  Please.']

In [26]:
#Define new path file
datafile = os.path.join("formatted_movie_lines.txt")
delimiter = '\t'

#Unescape the delimiter
delimiter = str(codecs.decode(delimiter, "unicode_escape"))

#Write the new csv file 
print('\nWriting newly formatted file...')

with open(datafile, "w", encoding = 'utf-8') as outputfile:
  writer = csv.writer(outputfile, delimiter = delimiter)
  for pair in qa_pairs:
    writer.writerow(pair)
print("Done writing file")


Writing newly formatted file...
Done writing file


In [27]:
with open(datafile, 'r') as file:
  lines = file.readlines()
for line in lines[:8]:
  print(line)

Can we make this quick?  Roxanne Korrine and Andrew Barrett are having an incredibly horrendous public break- up on the quad.  Again.	Well, I thought we'd start with pronunciation, if that's okay with you.

Well, I thought we'd start with pronunciation, if that's okay with you.	Not the hacking and gagging and spitting part.  Please.

Not the hacking and gagging and spitting part.  Please.	Okay... then how 'bout we try out some French cuisine.  Saturday?  Night?

You're asking me out.  That's so cute. What's your name again?	Forget it.

No, no, it's my fault -- we didn't have a proper introduction ---	Cameron.

Cameron.	The thing is, Cameron -- I'm at the mercy of a particularly hideous breed of loser.  My sister.  I can't date until she does.

The thing is, Cameron -- I'm at the mercy of a particularly hideous breed of loser.  My sister.  I can't date until she does.	Seems like she could get a date easy enough...

Why?	Unsolved mystery.  She used to be really popular when she started h

In [0]:
PAD_token = 0 #Used for padding short sentences 
SOS_token = 1 #Start of Sentence token
EOS_token = 2 # End of Sentence token

class Vocabulary:
  def __init__(self, name):
    self.name = name
    self.word2index = {}
    self.word2count = {}
    self.index2word = {PAD_token: 'PAD', SOS_token: 'SOS', EOS_token: 'EOS'}
    self.num_of_words = 3 #Count SOS, EOS, PAD

  def addSentence(self, sentence):
    for word in sentence.split(" "):
      self.addWord(word)

  def addWord(self, word):
    if word not in self.word2index:
      self.word2index[word] = self.num_of_words
      self.word2count[word] = 1
      self.index2word[self.num_of_words] = word
      self.num_of_words += 1
    
    else:
      self.word2count[word] += 1

  #Remove words below a certain count threshold 

  def trim(self, min):
    keep_words = []
    for k, v in self.word2count.items():
      if v >= min:
        keep_words.append(k)

    print('keep_words {}/{} = {:.4f}'.format(len(keep_words), len(self.word2index), len(keep_words)/len(self.word2index)))
    #Reinitialize dictionaries 
    self.word2index = {}
    self.word2count = {}
    self.index2word = {PAD_token: 'PAD', SOS_token: 'SOS', EOS_token: 'EOS'}
    self.num_of_words = 3 #Count SOS, EOS, PAD

    for word in keep_words:
      self.addWord(word)



In [0]:
# Turn a Unicode string to plain ASCII
def unicodeToAscii(s):
  return ''.join(c for c in unicodedata.normalize('NFD', s) if unicodedata.category(c) != 'Mn')

In [0]:
def normalizeString(s):
  s = unicodeToAscii(s.lower().strip())
  # Replace any .!? by a whitespace + the character --> '!' =  ' !'. \1 means the first bracketed group --> [.!?]. r is to
  #not consider \1 as a character (r to escape backslash). + means one or more 
  s = re.sub(r"([.!?])", r" \1", s)
  # Remove any character that is not a sequence of lower or upper case letters
  s = re.sub(r"[^a-zA-Z.!?]+", r" ", s)
  # Remove a sequence of white space characters
  s = re.sub(r"\s+", r" ",s).strip()
  return s

In [31]:
#Test the function
normalizeString("aaaa123556!ssd's dd?")

'aaaa !ssd s dd ?'

In [32]:
datafile = os.path.join("formatted_movie_lines.txt")
#Read the file and split into lines
print("Reading and Processing File ... Please Wait") 
f_lines = open(datafile, encoding = 'utf-8').read().strip().split('\n')
#Split everyline into pairs and normalize
pairs = [[normalizeString(s) for s in pair.split("\t")] for pair in f_lines]
print("Done Reading")



Reading and Processing File ... Please Wait
Done Reading


In [0]:
voc = Vocabulary("cornell movie-dialogs corpus")

In [34]:
pairs[0]

['can we make this quick ? roxanne korrine and andrew barrett are having an incredibly horrendous public break up on the quad . again .',
 'well i thought we d start with pronunciation if that s okay with you .']

In [35]:
len(pairs)

221282

In [0]:
# Select pair of Sentences that are below the maximum length
Max_Length = 10

def filterPair(p):
  return len(p[0].split()) < Max_Length and len(p[1].split()) < Max_Length

def filterPairs(pairs):
  return [pair for pair in pairs if filterPair(pair)]

In [37]:
print("there are {} conversations before filtering".format(len(pairs)))
pairs = filterPairs(pairs)
print("there are {} conversations after filtering".format(len(pairs)))

there are 221282 conversations before filtering
there are 64271 conversations after filtering


In [38]:
# Loop through each pair of and add the question and reply sentence to the vocabulary
for pair in pairs:
  voc.addSentence(pair[0])
  voc.addSentence(pair[1])

print("Counted word = ", voc.num_of_words)
for pair in pairs[:10]:
  print(pair)


Counted word =  18008
['there .', 'where ?']
['you have my word . as a gentleman', 'you re sweet .']
['hi .', 'looks like things worked out tonight huh ?']
['you know chastity ?', 'i believe we share an art instructor']
['have fun tonight ?', 'tons']
['well no . . .', 'then that s all you had to say .']
['then that s all you had to say .', 'but']
['but', 'you always been this selfish ?']
['do you listen to this crap ?', 'what crap ?']
['what good stuff ?', 'the real you .']


In [0]:
def trim_rare_words(voc, pairs, min_count):
  #Trim words used under the min_count 
  voc.trim(min_count)
  #Filter out pairs with trimmed words
  keep_pairs = []

  for pair in pairs:
    keep_input = True
    keep_output = True
    input_sentence = pair[0]
    output_sentence = pair[1]
    #Check input sentences
    for word in input_sentence.split():
      if word not in voc.word2index:
        keep_input = False 
        break
    #check output sentences
    for word in output_sentence.split():
      if word not in voc.word2index:
        keep_output = False
        break

    if keep_input and keep_output:
      keep_pairs.append(pair)

  

  print("Trained form {} pairs to {} pairs, {:.4f} of figures".format(len(pairs), len(keep_pairs), len(keep_pairs)/len(pairs)))

  return keep_pairs



In [40]:
pairs[1][0]

'you have my word . as a gentleman'

In [41]:
pairs = trim_rare_words(voc, pairs, 3)

keep_words 7823/18005 = 0.4345
Trained form 64271 pairs to 53165 pairs, 0.8272 of figures


In [42]:
pairs[1][0]

'you have my word . as a gentleman'

In [0]:
def index_from_sentence (voc, sentence):
  return [voc.word2index[word] for word in sentence.split()] + [EOS_token]

In [44]:
index_from_sentence (voc, pairs[1][0])

[7, 8, 9, 10, 4, 11, 12, 13, 2]

In [45]:
#Define some samples for testing
inp = []
out = []
for pair in pairs[:10]:
  inp.append(pair[0])
  out.append(pair[1])

print(inp)
print(len(inp))

indexes = [index_from_sentence(voc, sentence) for sentence in inp]
indexes

['there .', 'you have my word . as a gentleman', 'hi .', 'have fun tonight ?', 'well no . . .', 'then that s all you had to say .', 'but', 'do you listen to this crap ?', 'what good stuff ?', 'wow']
10


[[3, 4, 2],
 [7, 8, 9, 10, 4, 11, 12, 13, 2],
 [16, 4, 2],
 [8, 31, 22, 6, 2],
 [33, 34, 4, 4, 4, 2],
 [35, 36, 37, 38, 7, 39, 40, 41, 4, 2],
 [42, 2],
 [47, 7, 48, 40, 45, 49, 6, 2],
 [50, 51, 52, 6, 2],
 [58, 2]]

In [46]:
a = [[3, 4, 2],
 [7, 8, 9, 10, 4, 11, 12, 13, 2],
 [16, 4, 2],
 [8, 31, 22, 6, 2],
 [33, 34, 4, 4, 4, 2],
 [35, 36, 37, 38, 7, 39, 40, 41, 4, 2],
 [42, 2],
 [47, 7, 48, 40, 45, 49, 6, 2],
 [50, 51, 52, 6, 2],
 [58, 2]]

a

[[3, 4, 2],
 [7, 8, 9, 10, 4, 11, 12, 13, 2],
 [16, 4, 2],
 [8, 31, 22, 6, 2],
 [33, 34, 4, 4, 4, 2],
 [35, 36, 37, 38, 7, 39, 40, 41, 4, 2],
 [42, 2],
 [47, 7, 48, 40, 45, 49, 6, 2],
 [50, 51, 52, 6, 2],
 [58, 2]]

In [47]:
list(itertools.zip_longest(*a, fillvalue = 0))

[(3, 7, 16, 8, 33, 35, 42, 47, 50, 58),
 (4, 8, 4, 31, 34, 36, 2, 7, 51, 2),
 (2, 9, 2, 22, 4, 37, 0, 48, 52, 0),
 (0, 10, 0, 6, 4, 38, 0, 40, 6, 0),
 (0, 4, 0, 2, 4, 7, 0, 45, 2, 0),
 (0, 11, 0, 0, 2, 39, 0, 49, 0, 0),
 (0, 12, 0, 0, 0, 40, 0, 6, 0, 0),
 (0, 13, 0, 0, 0, 41, 0, 2, 0, 0),
 (0, 2, 0, 0, 0, 4, 0, 0, 0, 0),
 (0, 0, 0, 0, 0, 2, 0, 0, 0, 0)]

In [48]:
leng = [len(ind) for ind in indexes]
max(leng)

10

In [49]:
leng

[3, 9, 3, 5, 6, 10, 2, 8, 5, 2]

In [0]:
def zero_padding (l, fillvalue = 0):
  return list(itertools.zip_longest(*l, fillvalue = fillvalue))

In [51]:
test_result = zero_padding(indexes)
test_result

[(3, 7, 16, 8, 33, 35, 42, 47, 50, 58),
 (4, 8, 4, 31, 34, 36, 2, 7, 51, 2),
 (2, 9, 2, 22, 4, 37, 0, 48, 52, 0),
 (0, 10, 0, 6, 4, 38, 0, 40, 6, 0),
 (0, 4, 0, 2, 4, 7, 0, 45, 2, 0),
 (0, 11, 0, 0, 2, 39, 0, 49, 0, 0),
 (0, 12, 0, 0, 0, 40, 0, 6, 0, 0),
 (0, 13, 0, 0, 0, 41, 0, 2, 0, 0),
 (0, 2, 0, 0, 0, 4, 0, 0, 0, 0),
 (0, 0, 0, 0, 0, 2, 0, 0, 0, 0)]

In [0]:
def make_binary(l):
  b = []
  for i, val in enumerate(l):
    b.append([])
    for item in val:
      if item > 0:
        b[i].append(1)
      else:
        b[i].append(0)

  return b

In [0]:
binary_result = make_binary(test_result)

In [0]:
def input_var(l, voc):
  indexes_batch = [index_from_sentence(voc, sentence) for sentence in l]
  lengths = torch.tensor([len(indexes) for indexes in indexes_batch])
  pad_list = zero_padding(indexes_batch)
  pad_var = torch.LongTensor(pad_list)

  return pad_var, lengths


In [0]:
def output_var(l, voc):
  indexes_batch = [index_from_sentence(voc, sentence) for sentence in l]
  max_length = max([len(indexes) for indexes in indexes_batch])
  pad_list = zero_padding(indexes_batch)
  mask = make_binary(pad_list)
  mask = torch.ByteTensor(mask)
  pad_var = torch.LongTensor(pad_list)

  return pad_var, mask, max_length

In [0]:
def batch_2_train_data(voc, pairs):

  pairs.sort(key = lambda x: len(x[0].split()), reverse = True)
  input_batch, output_batch = [], []
  for pair in pairs:
    input_batch.append(pair[0])
    output_batch.append(pair[1])
    
  inp_var, length = input_var(input_batch, voc)
  out_var, mask, max_length = output_var(output_batch, voc)

  return inp_var, length, out_var, mask, max_length

In [57]:
#Testing the batch2train function 
batch_size = 10
batch = batch_2_train_data(voc, [random.choice(pairs) for _ in range(batch_size)])
inp_var, length, out_var, mask, max_length = batch

print("Input Variable")
print(inp_var)

print("Length")
print(length)

print("Target Variable")
print(out_var)

print("Mask")
print(mask)

print("Maximum Target Length")
max_length

Input Variable
tensor([[  38,   25, 6361,   25,  571,   25,   65,    7, 1596,   50],
        [ 266,   63,  829,   74,  572,  118,   14,  215,    4,    6],
        [  77,   45,   66,   25,   66,   40,   38,  598,    4,    2],
        [  14,  102,   76,  290,  401,  598,  468,    4,    4,    0],
        [   7,  782,  102,   60,  169,    4,    6,    2,    2,    0],
        [ 169,  169,   29,  480,   83,    2,    2,    0,    0,    0],
        [   6, 2886, 1086,    4,   66,    0,    0,    0,    0,    0],
        [1081, 6634,    4,    2,    2,    0,    0,    0,    0,    0],
        [   6,   66,    2,    0,    0,    0,    0,    0,    0,    0],
        [   2,    2,    0,    0,    0,    0,    0,    0,    0,    0]])
Length
tensor([10, 10,  9,  8,  8,  6,  6,  5,  5,  3])
Target Variable
tensor([[  34,   76,   29,   92,   34,  122, 1588,  167,   50,   50],
        [   4,  102, 1086,    7, 2556,   25,   37,   25,    6,  115],
        [   2,    4,    6,  869,  571,  197,  468,   24,    2,   53],
  

9

# Building Model 

In [0]:
class EncoderRNN(nn.Module):
  def __init__(self, hidden_size, embedding, n_layers=1, dropout = 0):
    super(EncoderRNN, self).__init__()
    self.n_layers = n_layers
    self.hidden_size = hidden_size
    self.embedding = embedding 
    # Initialize GRU; the input_size and the hidden_size params  are both set to "hidden_size"
    # because our input size is word embedding with number of features == hidden_size
    self.gru = nn.GRU(hidden_size, hidden_size, n_layers, dropout = (0 if n_layers == 1 else dropout), bidirectional = True)

  def forward(self, input_seq, input_lengths, hidden = None):
    # input_seq: batch of input sentences; shape =(max_length, batch_size)
    # input_lengths: list of sentence lengths corresponding to each sentence in the batch 
    # hidden_state of shape: (n_layers * num_direction, batch_size, hidden_size)
    # convert worn indexes to embeddings 
    embedded = self.embedding(input_seq)
    # pack padded batch of sequences for RNN model
    packed = torch.nn.utils.rnn.pack_padded_sequence(embedded, input_lengths)
    # forward pass through GPU
    outputs, hidden = self.gru(packed, hidden)
    # Unpack padding
    outputs, _ = torch.nn.utils.rnn.pad_packed_sequence(outputs)
    # sum bidirectional GRU outputs
    outputs = outputs[:, :, :self.hidden_size] + outputs[:, :, self.hidden_size:]

    # return output and final hidden state 
    return outputs, hidden

    # outputs: the output features h_t from the last layer of the GRU, for each timestep (sum of bidirectional outputs) 
    # outputs shape = (max_length, batch_size, hidden_size )
    # hidden: hidden state for the last timestamp, of shape = (n_layers * num_directions, batch_size, hidden_size)

In [0]:
class Attn (nn.Module):
  def __init__ (self, method, hidden_size):
    super(Attn, self).__init__()
    self.method = method
    self.hidden_size = hidden_size 

  def dot_score (self, hidden, encoder_output):
    #Element wise multiplication of the current hidden state outpute with the ncoder output
    return torch.sum(hidden * encoder_output, dim = 2)

  def forward (self, hidden, encoder_output):
    # hidden of shape (1, batch_size, hidden_size)
    # encoder_outputs of shape (max_length, batch_size, hidden_size)
    # (1, batch_size, hidden_size) * (max_length, batch_size, hidden_size) = (max_length, batch_size, hidden_size)

    #Calculate the attention weights 
    attn_energies = self.dot_score(hidden, encoder_output)  #(max_length, batch_size)

    attn_energies = attn_energies.t() #(batch_size, max_length)

    # Return the softmax normalized probability score with added dimension

    return F.softmax(attn_energies, dim = 1).unsqueeze(1)  #(batch_size, 1, max_length)

In [0]:
class Luong_Attn_Decoder (nn.Module):
  def __init__(self, attn_model, embedding, hidden_size, output_size, n_layers = 1, dropout = 0.1 ):
    super(Luong_Attn_Decoder, self).__init__()
    self.attn_model = attn_model
    self.hidden_size = hidden_size
    self.output_size = output_size
    self.n_layers = n_layers
    self.dropout = dropout 

    # Define layers 
    self.embedding = embedding
    self.embedding_dropout = nn.Dropout(dropout)
    self.gru = nn.GRU(hidden_size, hidden_size, n_layers, dropout = (0 if n_layers == 1 else dropout))
    self.concat = nn.Linear(hidden_size*2, hidden_size)
    self.out = nn.Linear(hidden_size, output_size)

    self.attn = Attn(attn_model, hidden_size)


  def forward (self, input_step, last_hidden, encoder_outputs):
    # input_step: one time stamp of input sequence batch; shape = (1, batch_size)
    # last_hidden: final hidden state of GRU; shape = (n_layers * num_directions, batch_size, hidden_size)
    # encoder_outputs: encoder model's output; shape = (max_length, batch, num_directions * hidden_size)
    # Note: We run this one timestamp at a time.
    
    # Get embedding of current input word
    embedded = self.embedding(input_step)
    embedded = self.embedding_dropout(embedded) 
    # Forward through unidirectional GRU
    rnn_output, hidden = self.gru(embedded, last_hidden)
    # rnn_output shape = (1, batch, num_direction * hidden_size)
    # hidden of shape = (n_layers * num_directions, batch, hidden_size)

    # Calculate the attention weight from the current GRU output
    attn_weight = self.attn(rnn_output, encoder_outputs)

    # Multiply attention weight to encoder_output to get new "Weighted sum" context vector
    # (batch_size, 1, max_length) bmm with (batch_size, max_length, hidden) = (batch_size, 1, hidden)
    context = attn_weight.bmm(encoder_outputs.transpose(0, 1))

    #concatenate weighted context vector and GRU output
    rnn_output = rnn_output.squeeze(0)
    context = context.squeeze(1)
    concat_input = torch.cat((rnn_output, context), 1)
    concat_output = torch.tanh(self.concat(concat_input))

    # predict next word using Luong eq. 6
    output = self.out(concat_output)
    output = F.softmax(output, dim = 1)
    # Return output and final hidden state 

    return output, hidden

    # output: softmax normalized tensor giving probabilities of each word being the correct next word in the decoded sequence 
    # shape = (batch_size, voc_size)
    # hidden: final hidden state of GRU; shape = (num_layers *num_directions, batch_size, hidden_size)



    

# Training the model 

In [0]:
def maskNLLloss(decoder_out, target, mask):
  nTotal = mask.sum()
  target = target.view(-1, 1)
  # decoder_out shape: (batch_size, voc_size), target_size = (batch_size, 1)
  gathered = torch.gather(decoder_out, 1, target)

  # Calculate the NLLL
  cross_entropy = -torch.log(gathered)
  # Seleect the non zero elements 
  loss = cross_entropy.masked_select(mask)

  loss = loss.mean()
  loss = loss.to(device)
  return loss, nTotal.item()


In [0]:
# Visualize whats happening in one iteratiion 
batch_size = 64
batches = batch_2_train_data(voc, [random.choice(pairs) for _ in range (batch_size)])
input_variable, lengths, target_variable, mask, max_target_len = batches

print("Input Variable Shape:", input_variable.shape )

print("Lengths Shape:", lengths.shape)

print("Target Variable Shape", target_variable.shape)

print("Mask Shape", mask.shape)

print("Maximum Target Length", max_target_len)

# Define the parameters 
hidden_size = 500
encoder_n_layers = 2
decoder_n_layers = 2
dropout = 0.1
embedding = nn.Embedding(voc.num_of_words, hidden_size)
attn_model = 'dot'

# Define the Encoder and Decoder 
encoder = EncoderRNN(hidden_size, embedding, encoder_n_layers, dropout)
decoder = Luong_Attn_Decoder(attn_model, embedding, hidden_size, voc.num_of_words, decoder_n_layers, dropout)
encoder = encoder.to(device)
decoder = decoder.to(device)

#Ensure dropout layers are in train mode 
encoder.train()
decoder.train()

#Initialize optimizers
encoder_optimizer = optim.Adam(encoder.parameters(), lr = 0.001)
decoder_optimizer = optim.Adam(decoder.parameters(), lr = 0.001)
encoder_optimizer.zero_grad()
decoder_optimizer.zero_grad()

input_variable = input_variable.to(device)
lengths = lengths.to(device)
target_variable = target_variable.to(device)
mask = mask.to(device)

loss = 0
print_losses = []
n_totals = 0

encoder_outputs, encoder_hidden = encoder(input_variable, lengths)
print("Encoder Output Shape", encoder_outputs.shape)
print("Last Encoder hidden Shape", encoder_hidden.shape)

decoder_input = torch.LongTensor([[SOS_token for _ in range (batch_size)]])#.unsqueeze(0)
decoder_input = decoder_input.to(device)
print("Initial Decoder Input Shape:", decoder_input.shape)
print(decoder_input)

# Set initial decoder hidden state to the encoder's final hidden state
decoder_hidden = encoder_hidden[:decoder.n_layers]
print ("Initial Decoder hidden state shape:", decoder_hidden.shape)
print('\n')
print("-------------------------------------------------------------------------------------")
print("Now lets see whats happening in every timestamp in the GRU")
print("-------------------------------------------------------------------------------------")
print("\n")

# Assume we are using Teacher forcing 
for t in range(max_target_len):
  decoder_output, decoder_hidden = decoder(decoder_input, decoder_hidden, encoder_outputs)
  print ("Decoder Output Shape:", decoder_output.shape)
  print ("Decoder Hidden Shape:", decoder_hidden.shape)

  # Teacher forcing: Next input == Current target
  decoder_input = target_variable[t].view(1, -1)
  print ("The target variable at the current timestamp before reshaping:", target_variable[t])
  print ("The target variable at the current timestamp shape before reshaping:", target_variable[t].shape)
  print ("The Decoder input shape (reshaped target variable)", decoder_input.shape)

  # Calculate and accumulate loss
  print ("The mask at the current timestep:", mask[t])
  print ("The mask at the current timestep shape", mask[t].shape)
  mask_loss, nTotal = maskNLLloss(decoder_output, target_variable[t], mask[t])
  print ("Mask Loss", mask_loss)
  print ('Total', nTotal)
  loss += mask_loss
  print_losses.append(mask_loss.item() * nTotal)
  print (print_losses)
  n_totals += nTotal
  print (n_totals)
  encoder_optimizer.step()
  decoder_optimizer.step()
  returned_loss = sum(print_losses)/ n_totals
  print("Returned Loss:", returned_loss)
  print("\n")
  print('----------------------------------DONE ONE TIMESTEP----------------------')
  print("\n")
  


NameError: ignored

In [0]:
def train (input_variable, lengths, target_variable, mask, max_target_len, encoder, decoder, embedding, 
           encoder_optimizer, decoder_optimizer, batch_size, clip, max_length = Max_Length):
  # Zero Gradients
  encoder_optimizer.zero_grad()
  decoder_optimizer.zero_grad()

  # Set Device option 
  input_variable = input_variable.to(device)
  lengths = lengths.to(device)
  target_variable = target_variable.to(device)
  mask = mask.to(device)

  # Initialize variables 
  loss = 0 
  print_losses = []
  n_totals = 0

  # Forward pass through encoder
  encoder_outputs, encoder_hidden = encoder(input_variable, lengths)

  # Create initial decoder input (start with SOS token for each sentence)
  decoder_input = decoder_input = torch.LongTensor([[SOS_token for _ in range (batch_size)]])
  decoder_input = decoder_input.to(device)

  # Set First Decoder hidden state to final encoder hiodden state 
  decoder_hidden = encoder_hidden[:decoder.n_layers]

  # Determine if we are using teacher forcing for this iteration 
  use_teacher_forcing = True if random.random() < teacher_forcing_ratio else False

  if use_teacher_forcing:
    for t in range(max_target_len):
      decoder_output, decoder_hidden = decoder(decoder_input, decoder_hidden, encoder_outputs)
      # Teacher forcing: Next input == Current target
      decoder_input = target_variable[t].view(1, -1)

      mask_loss, nTotal = maskNLLloss(decoder_output, target_variable[t], mask[t])
      loss += mask_loss
      print_losses.append(mask_loss.item() * nTotal)
      n_totals += nTotal

  else:
    for t in range(max_target_len):
      decoder_output, decoder_hidden = decoder(decoder_input, decoder_hidden, encoder_outputs)
      # Noteacher forcing: Next input is decoder's current output
      _, topi = decoder_output.topk(1)
      decoder_input = torch.LongTensor([[topi[i][0] for i in range(batch_size)]])
      decoder_input = input.to(device)

      mask_loss, nTotal = maskNLLloss(decoder_output, target_variable[t], mask[t])
      loss += mask_loss
      print_losses.append(mask_loss.item() * nTotal)
      n_totals += nTotal


  #perform backpropagation
  loss.backward()

  #Clip gradien: gradients are modified in place 
  _ = torch.nn.utils.clip_grad_norm_(encoder.parameters(), clip)
  _ = torch.nn.utils.clip_grad_norm_(decoder.parameters(), clip)

  # Adjust model weights 
  encoder_optimizer.step()
  decoder_optimizer.step()

  return sum(print_losses) / n_totals



In [0]:
def train_iters (model_name, voc, pairs, encoder, decoder, encoder_optimizer, decoder_optimizer, embedding,
                 encoder_n_layers, decoder_n_layers, save_dir, n_iteration, batch_size, print_every, save_every,
                 clip, corpus_name, loadFilename):
  
  # Load batches for each iteration 
  training_batches = [batch_2_train_data(voc, [random.choice(pairs) for _ in range(batch_size)]) for _ in range(n_iteration)]

  # Initializations 
  print("Initializing...")
  start_iteration = 1
  print_loss = 0 
  if loadFilename:
    start_iteration = checkpoint["iteration"] + 1

  # Training loop 
  print ("Training...")
  for iteration in range(start_iteration, n_iteration + 1):
    training_batch = training_batches[iteration - 1]
    # Extract fields from batch
    input_variable, lengths, target_variable, mask, max_target_len = training_batch

    # Run a training iteration with batch
    loss = train (input_variable, lengths, target_variable, mask, max_target_len, encoder, decoder, embedding, encoder_optimizer,
                  decoder_optimizer, batch_size, clip) 
    print_loss += loss

    # Print progress
    if iteration % print_every == 0:
      print_loss_avg = print_loss / print_every
      print("Iteration: {}; Percent Complete {:.1f}%; Average loss {:.4f}".format(iteration, iteration/ n_iteration * 100, print_loss_avg))
      print_loss = 0

    # Save Checkpoint 
    if (iteration % save_every == 0):
      directory = os.path.join(save_dir, model_name, corpus_name, '{}-{}_{}'.format(encoder_n_layers, decoder_n_layers, hidden_size))
      if not os.path.exists(directory):
        os.makedirs(directory)
      torch.save({'iteration': iteration, 'en': encoder.state_dict(), 'de': decoder.state_dict(), 'en_opt': encoder_optimizer.state_dict(),
                  'de_opt': decoder_optimizer.state_dict(), 'loss': loss, 'voc_dict': voc.__dict__,'embedding': embedding.state_dict()
                  }, os.path.join(directory, '{}_{}>tar'.format(iteration, 'checkpoint')))

In [0]:
class GreedySearchDecoder(nn.Module):
  def __init__(self, encoder, decoder):
    super(GreedySearchDecoder, self).__init__()
    self.encoder = encoder 
    self.decoder = decoder 

  def forward(self, input_seq, input_length, max_length):
    # Forward input through encoder model 
    encoder_outputs, encoder_hidden = self.encoder(input_seq, input_length)
    # Prepare Encoder's final hidden layer to be the first hidden layer input to the decoder 
    decoder_hidden = encoder_hidden[:decoder.n_layers]
    # Initialize decoder input with SOS token 
    decoder_input = torch.ones (1, 1, device = device, dtype = torch.long) * SOS_token
    # Initialize tensors to append decoded word to
    all_tokens = torch.zeros([0], device = device, dtype = torch.long)
    all_scores = torch.zeros([0], device = device)
    # Iteratively decide one word token at a time
    for _ in range (max_length):
      # Foward pass through decoder
      decoder_output, decoder_hidden = self.decoder(decoder_input, decoder_hidden, encoder_outputs)
      # Obtain most likely word token and its softmax score 
      decoder_scores, decoder_input = torch.max(decoder_output, dim = 1)
      # Record token and score
      all_tokens = torch.cat((all_tokens, decoder_input), dim = 0)
      all_scores = torch.cat((all_scores, decoder_scores), dim = 0)
      #prepare current token to bethe next decoder input (add a dimension)
      decoder_input = torch.unsqueeze(decoder_input, 0)

    #Return collectiion of word tokens and scores 
    return all_tokens, all_scores 
    



In [0]:
def evaluate (encoder, decoder, searcher, voc, sentence, max_length = Max_Length):
  ### Format input sentence as a batch 
  # words -> indexes 
  indexes_batch = [index_from_sentence(voc, sentence)]
  # Create length tensor 
  lengths = torch.tensor([len(indexes) for indexes in indexes_batch])
  # Transpose dimensions of batch to model's expectation 
  input_batch = torch.LongTensor(indexes_batch).transpose(0, 1)
  # Use appropriate device 
  input_batch = input_batch.to(device)
  lengths = lengths.to(device)
  # Decode sentence with searcher 
  tokens, scores = searcher(input_batch, lengths, max_length)
  # indexes -> words
  decoded_words = [voc.index2word[token.item()] for token in tokens]
  return decoded_words 

def evaluateInput (encoder, decoder, searcher, voc):
  input_sentence = ''
  while (1):
    try:
      # Get input sentence 
      input_sentence = input('>')
      # Check if it is quit case 
      if input_sentence == 'q' or input_sentence == 'quit': break
      # Normalize sentence 
      input_sentence = normalizeString(input_sentence)
      # Evaluate sentence
      output_words = evaluate (encoder, decoder, searcher, voc, input_sentence)
      # Format and print response sentence
      output_words[:] = [x for x in output_words if not(x == 'EOS' or x =='PAD')] 
      print('Bot:', ''.join(output_words))

    except KeyError:
      print ('Error: Encountered unknown word')

In [85]:
# Configure model 
model_name = 'cb_model'
attn_model = 'dot'
#attn_model = 'general'
#attn_model = 'concat'
hidden_size = 500
encoder_n_layers = 2
decoder_n_layers = 2
dropout = 0.1
batch_size = 64

# Set checkpoint to load from; set to None if starting from the scratch
loadFilename = None 
checkpoint_iter = 4000
#loadFilename = os.path.join(save_dir, model_name, corpus_name, '{}-{}_{}'.format(encoder_n_layers, decoder_n_layers, hidden_size),
#                            '{}_checkpoint.tar'.format(checkpoint_iter))

# Load model if a loadFilename is provided
if loadFilename:
  # if loading on same machine the model was trained on 
  checkpoint = torch.load(loadFilename)
  # if loading a model trained on GPU to CPU
  #checkpoint = torch.load(loadFilename, map_location = torch.device('cpu'))
  encoder_sd = checkpoint['en']
  decoder_sd = checkpoint['de']
  encoder_optimizer_sd = checkpoint['en_opt']
  decoder_optimizer_sd = checkpoint['de_opt']
  embedding_sd = checkpoint['embedding']
  voc.__dict__ = checkpoint['voc_dict']  


print ('Building encoder and decoder...')
# Initialize word embeddings
embeddings = nn.Embedding(voc.num_of_words, hidden_size)
if loadFilename:
  embedding.load_state_dict(embedding_sd)
# Initialize encoder & decoder models 
encoder = EncoderRNN(hidden_size, embeddings, encoder_n_layers, dropout)
decoder = Luong_Attn_Decoder(attn_model, embeddings, hidden_size, voc.num_of_words, decoder_n_layers, dropout)
if loadFilename:
  encoder.load_state_dict(encoder_sd)
  decoder.load_state_dict(decoder_sd)

# Use appropriate device 
encoder = encoder.to(device)
decoder = decoder.to(device)
print('Models built and ready to go!')

Building encoder and decoder...
Models built and ready to go!


In [86]:
# Configure training/optimization
clip = 50.0
teacher_forcing_ratio = 1.0
learning_rate = 0.0001
decoder_learning_ratio = 5.0
n_iteration = 4000
print_every = 1
save_every = 500
save_dir = "chatbot.py"
model_name = "Basic chatbot"
corpus_name = "cornell"


# Ensure dropout layers are in train mode 
encoder.train()
decoder.train()

#Initialize optimizers 
print('Building optimizers...')
encoder_optimizer = optim.Adam(encoder.parameters(), lr = learning_rate)
decoder_optimizer = optim.Adam(decoder.parameters(), lr = learning_rate * decoder_learning_ratio)
if loadFilename:
  encoder_optimizer.load_state_dict(encoder_optimizer_sd)
  decoder_optimizer.load_state_dict(decoder_optimizer_sd)

# if you have cuda, configure cuda to call
for state in encoder_optimizer.state.values():
  for k, v in state.items():
    if isinstance(v, torch.Tensor):
      state[k] = v.cuda()

for state in decoder_optimizer.state.values():
  for k, v in state.items():
    if isinstance(v, torch.Tensor):
      state[k] = v.cuda()



# Run training iterations
print('Starting Training!')
train_iters(model_name, voc, pairs, encoder, decoder, encoder_optimizer, decoder_optimizer, embeddings, encoder_n_layers, decoder_n_layers, save_dir, n_iteration, batch_size, print_every, save_every, clip, corpus_name, loadFilename)



Building optimizers...
Starting Training!
Initializing...
Training...
Iteration: 1; Percent Complete 0.0%; Average loss 8.9562
Iteration: 2; Percent Complete 0.1%; Average loss 8.7591
Iteration: 3; Percent Complete 0.1%; Average loss 8.4053


/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,plea

Iteration: 4; Percent Complete 0.1%; Average loss 7.9939
Iteration: 5; Percent Complete 0.1%; Average loss 7.2809
Iteration: 6; Percent Complete 0.1%; Average loss 6.9740
Iteration: 7; Percent Complete 0.2%; Average loss 6.8240
Iteration: 8; Percent Complete 0.2%; Average loss 6.7780


/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,plea

Iteration: 9; Percent Complete 0.2%; Average loss 6.5067
Iteration: 10; Percent Complete 0.2%; Average loss 6.2377
Iteration: 11; Percent Complete 0.3%; Average loss 6.1380
Iteration: 12; Percent Complete 0.3%; Average loss 5.5632
Iteration: 13; Percent Complete 0.3%; Average loss 5.6161


...

Iteration: 3990; Percent Complete 99.8%; Average loss 2.2520
Iteration: 3991; Percent Complete 99.8%; Average loss 2.2488
Iteration: 3992; Percent Complete 99.8%; Average loss 2.0540
Iteration: 3993; Percent Complete 99.8%; Average loss 2.2638
Iteration: 3994; Percent Complete 99.9%; Average loss 2.2347


/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,plea

Iteration: 3995; Percent Complete 99.9%; Average loss 2.4223
Iteration: 3996; Percent Complete 99.9%; Average loss 2.0262
Iteration: 3997; Percent Complete 99.9%; Average loss 2.0915
Iteration: 3998; Percent Complete 100.0%; Average loss 2.1396
Iteration: 3999; Percent Complete 100.0%; Average loss 2.2235


/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,plea

Iteration: 4000; Percent Complete 100.0%; Average loss 1.9939


In [0]:
# Set dropout layers to eval mode
encoder.eval()
decoder.eval()

# Initialize search module
searcher = GreedySearchDecoder(encoder, decoder)

# Begin chatting (uncomment and run the following line to begin)
evaluateInput(encoder, decoder, searcher, voc)

Bot: imfine.
Bot: imsure.
Bot: blue.
Bot: imsorry.
Bot: idontknow.
Error: Encountered unknown word
Bot: idontknow.
Error: Encountered unknown word
Bot: imabowler.
